# Step 1. Download the data and prepare it for analysis

## Project description
As an internship in the analytical department at Yandex.Afisha our first task is to help optimize marketing expenses.


## Import

In [1297]:
try:
    !pip install -U plotly==5.5.0
    import plotly.express as px
except:
    !pip install plotly==5.5.0 #installing plotly
    import plotly.express as px

In [1298]:
pip install sidetable

Note: you may need to restart the kernel to use updated packages.


In [1299]:
import pandas as pd
import numpy as np
import plotly.express as px
from scipy import stats as st
import matplotlib.pyplot as plt
import sidetable
import seaborn as sns

%matplotlib inline

## Load data

In [1300]:
try:
    visits = pd.read_csv('visits_log_us.csv')
except:
    visits = pd.read_csv('/datasets/visits_log_us.csv')

try:
    orders = pd.read_csv('orders_log_us.csv')
except:
    orders = pd.read_csv('/datasets/orders_log_us.csv')
    
try:
    costs = pd.read_csv('costs_us.csv')
except:
    costs = pd.read_csv('/datasets/costs_us.csv')
                         

## prepare data for analysis

### visits

The visits table (server logs with data on website visits):
- Uid — user's unique identifier
- Device — user's device
- Start Ts — session start date and time
- End Ts — session end date and time
- Source Id — identifier of the ad source the user came from

In [1301]:
visits.head()

Device               End Ts  Source Id             Start Ts  \
0    touch  2017-12-20 17:38:00          4  2017-12-20 17:20:00   
1  desktop  2018-02-19 17:21:00          2  2018-02-19 16:53:00   
2    touch  2017-07-01 01:54:00          5  2017-07-01 01:54:00   
3  desktop  2018-05-20 11:23:00          9  2018-05-20 10:59:00   
4  desktop  2017-12-27 14:06:00          3  2017-12-27 14:06:00   

                    Uid  
0  16879256277535980062  
1    104060357244891740  
2   7459035603376831527  
3  16174680259334210214  
4   9969694820036681168

In [1302]:
visits.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   Device     359400 non-null  object
 1   End Ts     359400 non-null  object
 2   Source Id  359400 non-null  int64 
 3   Start Ts   359400 non-null  object
 4   Uid        359400 non-null  uint64
dtypes: int64(1), object(3), uint64(1)
memory usage: 13.7+ MB


In [1303]:
visits['Device'].value_counts()

desktop    262567
touch       96833
Name: Device, dtype: int64

In [1304]:
visits['Device'] = visits['Device'].astype('category')

In [1305]:
visits['Start Ts'] =  pd.to_datetime(visits['Start Ts'], format="%Y-%m-%d %H:%M:%S")
visits['End Ts'] =  pd.to_datetime(visits['End Ts'], format="%Y-%m-%d %H:%M:%S") 

In [1306]:
visits.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
 #   Column     Non-Null Count   Dtype         
---  ------     --------------   -----         
 0   Device     359400 non-null  category      
 1   End Ts     359400 non-null  datetime64[ns]
 2   Source Id  359400 non-null  int64         
 3   Start Ts   359400 non-null  datetime64[ns]
 4   Uid        359400 non-null  uint64        
dtypes: category(1), datetime64[ns](2), int64(1), uint64(1)
memory usage: 11.3 MB


Reduced +2MB and format data type

### orders

The orders table (data on orders):
- Uid — unique identifier of the user making an order
- Buy Ts — order date and time
- Revenue — Yandex.Afisha's revenue from the order

In [1307]:
orders.head()

Buy Ts  Revenue                   Uid
0  2017-06-01 00:10:00    17.00  10329302124590727494
1  2017-06-01 00:25:00     0.55  11627257723692907447
2  2017-06-01 00:27:00     0.37  17903680561304213844
3  2017-06-01 00:29:00     0.55  16109239769442553005
4  2017-06-01 07:58:00     0.37  14200605875248379450

In [1308]:
orders.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   Buy Ts   50415 non-null  object 
 1   Revenue  50415 non-null  float64
 2   Uid      50415 non-null  uint64 
dtypes: float64(1), object(1), uint64(1)
memory usage: 1.2+ MB


In [1309]:
orders['Buy Ts'] =  pd.to_datetime(orders['Buy Ts'], format="%Y-%m-%d %H:%M:%S")

In [1310]:
orders.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype         
---  ------   --------------  -----         
 0   Buy Ts   50415 non-null  datetime64[ns]
 1   Revenue  50415 non-null  float64       
 2   Uid      50415 non-null  uint64        
dtypes: datetime64[ns](1), float64(1), uint64(1)
memory usage: 1.2 MB


Reduced size by portion and format data type

### costs

The costs table (data on marketing expenses):
- source_id — ad source identifier
- dt — date
- costs — expenses on this ad source on this day

In [1311]:
costs.head()

source_id          dt  costs
0          1  2017-06-01  75.20
1          1  2017-06-02  62.25
2          1  2017-06-03  36.53
3          1  2017-06-04  55.00
4          1  2017-06-05  57.08

In [1312]:
costs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   source_id  2542 non-null   int64  
 1   dt         2542 non-null   object 
 2   costs      2542 non-null   float64
dtypes: float64(1), int64(1), object(1)
memory usage: 59.7+ KB


In [1313]:
costs['dt'] =  pd.to_datetime(costs['dt'], format="%Y-%m-%d")

In [1314]:
costs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   source_id  2542 non-null   int64         
 1   dt         2542 non-null   datetime64[ns]
 2   costs      2542 non-null   float64       
dtypes: datetime64[ns](1), float64(1), int64(1)
memory usage: 59.7 KB


Reduced size by portion and format data type

# Step 2. Make reports and calculate metrics:

## Product

### How many people use it every day, week, and month?

In [1315]:
visits.head()

Device              End Ts  Source Id            Start Ts  \
0    touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00   
1  desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00   
2    touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   
3  desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00   
4  desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   

                    Uid  
0  16879256277535980062  
1    104060357244891740  
2   7459035603376831527  
3  16174680259334210214  
4   9969694820036681168

In [1316]:
visits['session_year']  = visits['Start Ts'].dt.year
visits['session_month'] = visits['Start Ts'].dt.month
visits['session_week']  = visits['Start Ts'].dt.week
visits['session_date'] = visits['Start Ts'].dt.date

C:\Users\nirga\AppData\Local\Temp/ipykernel_8016/3083176516.py:3: FutureWarning:

Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.



There are three main metrics that describe the number of active users:
- DAU — the number of daily active (unique) users
- WAU — the number of weekly active users
- MAU — the number of monthly active users

In [1317]:
dau_total = visits.groupby('session_date').agg({'Uid': 'nunique'}).mean()
wau_total = visits.groupby(['session_year', 'session_week']).agg({'Uid': 'nunique'}).mean()
mau_total = visits.groupby(['session_year', 'session_month']).agg({'Uid': 'nunique'}).mean()

In [1318]:
print(int(dau_total), 'people use app every day')
print(int(wau_total), 'people use app every week') 
print(int(mau_total), 'people use app every month') 

907 people use app every day
5716 people use app every week
23228 people use app every month


### How many sessions are there per day? (One user might have more than one session.)

In [1319]:
sessions_per_day_total = visits.groupby('session_date').agg({'Uid': 'count'}).mean()

In [1320]:
print(int(sessions_per_day_total), 'sessions happen on the app every day')

987 sessions happen on the app every day


### What is the length of each session?

In [1321]:
visits['session_duration_sec'] = ((
    visits['End Ts'] - visits['Start Ts']).dt.seconds
)

In [1322]:
fig = px.histogram(visits.query('session_duration_sec < 6000'), x="session_duration_sec")
fig.show()

When the distribution is NOT normal or close to normal the mean or median dosn't work. So we will aplly mode.

In [1323]:
print('The most common session lengh is', int(visits['session_duration_sec'].mode()), 'seconds')

The most common session lengh is 60 seconds


### How often do users come back?

The sticky factor tells us how loyal the audience is - how often they return to the app. The formula is simple: sticky factor = DAU/WAU or sticky factor = DAU/MAU

In [1324]:
sticky_wau = dau_total/ wau_total*100
sticky_mau = dau_total/ mau_total*100

In [1325]:
print(f'{int(sticky_wau)}% of users remained active during whole week')
print(f'{int(sticky_mau)}% of users remained active during whole month')

15% of users remained active during whole week
3% of users remained active during whole month


## Sales

### When do people start buying?
In KPI analysis, we're usually interested in knowing the time that elapses between registration and conversion — when the user becomes a customer. For example, if registration and the first purchase occur on the same day, the user might fall into category Conversion 0d. If the first purchase happens the next day, it will be Conversion 1d. You can use any approach that lets you compare the conversions of different cohorts, so that you can determine which cohort, or marketing channel, is most effective.

Here we will compare the mean time in hours it took user to buy from first visit for each Source Id — identifier of the ad source the user came from. 

In [1326]:
visits['Source Id'].value_counts()

4     101794
3      85610
5      66905
2      47626
1      34121
9      13277
10     10025
7         36
6          6
Name: Source Id, dtype: int64

We will remove the Source Id from the analysis because they negligible

In [1327]:
first_visit = visits[['Source Id', 'Start Ts', 'Uid']]
first_visit = first_visit.groupby(['Uid'])['Start Ts'].min()
first_visit.name = 'first_visit_time'
first_visit.to_frame()
type(first_visit)
first_purchase = orders.merge(first_visit, on='Uid')
first_purchase['time_untill_first_buy'] = (
    first_purchase['Buy Ts'] - first_purchase['first_visit_time']
)
#first_purchase = first_purchase.query('time_untill_first_buy > 0')

In [1328]:
first_purchase['time_untill_first_buy'] = first_purchase['time_untill_first_buy'].dt.seconds

In [1329]:
first_purchase['time_untill_first_buy'][0]
first_purchase.rename(columns={'time_untill_first_buy': 'seconds_untill_first_buy'}, inplace=True)

In [1330]:
first_purchase.query('seconds_untill_first_buy > 0', inplace=True)

In [1331]:
first_purchase = first_purchase.merge(visits, on='Uid')

#first_purchase = first_purchase.groupby([])

In [1332]:
first_purchase = first_purchase[['Source Id', 'seconds_untill_first_buy']].reset_index()

In [1333]:
first_purchase = first_purchase.groupby('Source Id')['seconds_untill_first_buy'].mean()
first_purchase.name = 'maean_seconds_untill_first_buy'
first_purchase = first_purchase.to_frame()
first_purchase['maean_houres_untill_first_buy'] = first_purchase['maean_seconds_untill_first_buy']/60/60

In [1334]:
first_purchase

maean_seconds_untill_first_buy  maean_houres_untill_first_buy
Source Id                                                               
1                            32620.290042                       9.061192
2                            37942.802791                      10.539667
3                            33940.799371                       9.428000
4                            34252.667381                       9.514630
5                            32869.449485                       9.130403
7                             3120.000000                       0.866667
9                            34532.719692                       9.592422
10                           27527.093292                       7.646415

Remove Source id 7 because the amount of users in this source is negligible

In [1335]:
first_purchase.drop(index=([7]), inplace=True)

In [1336]:
fig = px.bar(first_purchase, y='maean_houres_untill_first_buy')
fig.show()

The mean time people start by is about 9 hr but for Source id 10 it was took the shortest mean time. less than 8 hr

### How many orders do they make during a given period of time?

In [1337]:
orders.head()

Buy Ts  Revenue                   Uid
0 2017-06-01 00:10:00    17.00  10329302124590727494
1 2017-06-01 00:25:00     0.55  11627257723692907447
2 2017-06-01 00:27:00     0.37  17903680561304213844
3 2017-06-01 00:29:00     0.55  16109239769442553005
4 2017-06-01 07:58:00     0.37  14200605875248379450

In [1338]:
orders['order_year']  = orders['Buy Ts'].dt.year
orders['order_month'] = orders['Buy Ts'].dt.month
orders['order_week']  = orders['Buy Ts'].dt.week
orders['order_date'] = orders['Buy Ts'].dt.date

C:\Users\nirga\AppData\Local\Temp/ipykernel_8016/2252360365.py:3: FutureWarning:

Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.



In [1339]:
orders.head()

Buy Ts  Revenue                   Uid  order_year  order_month  \
0 2017-06-01 00:10:00    17.00  10329302124590727494        2017            6   
1 2017-06-01 00:25:00     0.55  11627257723692907447        2017            6   
2 2017-06-01 00:27:00     0.37  17903680561304213844        2017            6   
3 2017-06-01 00:29:00     0.55  16109239769442553005        2017            6   
4 2017-06-01 07:58:00     0.37  14200605875248379450        2017            6   

   order_week  order_date  
0          22  2017-06-01  
1          22  2017-06-01  
2          22  2017-06-01  
3          22  2017-06-01  
4          22  2017-06-01

In [1340]:
orders_per_month = orders.groupby('order_month')['Uid'].count()

In [1341]:
orders_per_month.name = 'orders_per_month'

In [1342]:
orders_per_month = orders_per_month.to_frame()

In [1343]:
orders_per_month

orders_per_month
order_month                  
1                        4721
2                        5281
3                        5326
4                        3273
5                        4346
6                        2355
7                        2363
8                        1807
9                        3387
10                       5679
11                       5659
12                       6218

In [1344]:
fig = px.bar(orders_per_month, y='orders_per_month')
fig.show()

During sumer times orders drop. People don't buy culture during summer?

### What is the average purchase size?

In [1345]:
print('the average purchase size is', round(orders['Revenue'].mean(), 2))

the average purchase size is 5.0


In [1346]:
purchase_per_month = orders.groupby('order_month')['Revenue'].mean()

In [1347]:
purchase_per_month.name = 'purchase_per_month'

In [1348]:
purchase_per_month = purchase_per_month.to_frame()

In [1349]:
fig = px.bar(purchase_per_month, y='purchase_per_month')
fig.show()

We see in January and June decline in revenue and in the end of the month the revenue picks

### How much money do they bring? (LTV)

In [1350]:
orders.sample(3)

Buy Ts  Revenue                   Uid  order_year  \
21285 2017-12-01 11:12:00     1.47   1240664369974775312        2017   
27592 2018-01-01 23:24:00     0.98   2653293200440747297        2018   
35110 2018-02-15 22:05:00     3.05  10583814975819130304        2018   

       order_month  order_week  order_date  
21285           12          48  2017-12-01  
27592            1           1  2018-01-01  
35110            2           7  2018-02-15

Let's retrieve the month of each customer's first purchase:

In [1351]:
first_orders = orders.groupby('Uid').agg({'order_month': 'min'}).reset_index()
first_orders.columns = ['Uid', 'first_order_month']
first_orders.sample(3)

Uid  first_order_month
17521   8852842720653932085                 10
1534     771004267979090454                 10
29228  14743432370708170343                  1

We'll calculate the number of new customers (n_buyers) for each month:

In [1352]:
cohort_sizes = first_orders.groupby('first_order_month').agg({'Uid': 'nunique'}).reset_index()
cohort_sizes.columns = ['first_order_month', 'n_buyers']
cohort_sizes.sample(3)

first_order_month  n_buyers
11                 12      4015
8                   9      2383
7                   8      1245

Let's build cohorts. We'll add customers' first-purchase months to the table of orders:

In [1353]:
orders_ = pd.merge(orders,first_orders, on='Uid')
orders_.sample(3)

Buy Ts  Revenue                   Uid  order_year  \
25266 2017-12-01 23:18:00     1.47  16457876125703242311        2017   
34950 2018-02-26 12:42:00     4.53   5428360267575446305        2018   
46096 2018-04-20 12:45:00     6.11  18420448670844770365        2018   

       order_month  order_week  order_date  first_order_month  
25266           12          48  2017-12-01                 11  
34950            2           9  2018-02-26                  1  
46096            4          16  2018-04-20                  4

Now we'll group the table of orders by month of first purchase and month of purchase and sum up the revenue. We'll set the index to the default using the reset_index() method:

In [1354]:
cohorts = orders_.groupby(['first_order_month','order_month']).agg({'Revenue': 'sum'}).reset_index()
cohorts.sample(3)

first_order_month  order_month  Revenue
4                   1            5  2676.91
60                  7           10   394.43
22                  2           12   684.62

For purposes of cohort analysis, LTV is a cohort's cumulative revenue, accounting for the number of people in the cohort. Let's add data on how many users made their first purchases in each month to the cohorts table:

In [1355]:
report = pd.merge(cohort_sizes, cohorts, on='first_order_month')
report.head() 

first_order_month  n_buyers  order_month   Revenue
0                  1      3898            1  19417.13
1                  1      3898            2   8275.63
2                  1      3898            3   7970.76
3                  1      3898            4   3697.85
4                  1      3898            5   2676.91

LTV is a relative parameter, and it's easier to study for "mature" cohorts, so let's make the columns show the cohort's age instead of the month of the order. We will assume margin rate of 50%

In [1356]:
margin_rate = 0.5

report['gp'] = report['Revenue'] * margin_rate
report['age'] = (
    report['order_month'] - report['first_order_month']
) 
report['age'] = report['age'].round().astype('int')
report.head()

first_order_month  n_buyers  order_month   Revenue        gp  age
0                  1      3898            1  19417.13  9708.565    0
1                  1      3898            2   8275.63  4137.815    1
2                  1      3898            3   7970.76  3985.380    2
3                  1      3898            4   3697.85  1848.925    3
4                  1      3898            5   2676.91  1338.455    4

Now we can finally calculate LTV. Let's divide the cohort's gross profit for each month by the total number of users in each cohort. We'll visualize the cohorts as a pivot table to make things clear:

In [1358]:
report['ltv'] = report['gp'] / report['n_buyers']*100 # convert to cents

output = report.pivot_table(
    index='first_order_month', columns='age', values='ltv', aggfunc='mean'
).round()

output.fillna('') 

age                   0      1      2     3     4    5     6     7     8   \
first_order_month                                                           
1                  249.0  106.0  102.0  47.0  34.0  7.0  10.0  12.0  51.0   
2                  213.0   27.0    8.0   9.0   3.0  5.0   4.0  11.0  12.0   
3                  242.0   16.0   16.0   1.0   4.0  3.0   4.0  14.0  10.0   
4                  232.0   26.0    2.0   1.0   3.0  3.0   4.0   5.0   3.0   
5                  233.0    1.0    4.0   5.0   4.0  6.0   4.0   4.0         
6                  226.0    8.0    6.0   8.0   7.0  6.0   3.0               
7                  290.0    9.0   12.0  11.0   4.0  4.0                     
8                  254.0   11.0   11.0   8.0   5.0                          
9                  248.0   25.0    8.0  10.0                                
10                 239.0   15.0    5.0                                      
11                 253.0    9.0                                             
12                 221.0                                                    

age                  9     10     11  
first_order_month                     
1                  51.0  51.0  193.0  
2                  10.0   8.0         
3                   7.0               
4                                     
5                                     
6                                     
7                                     
8                                     
9                                     
10                                    
11                                    
12

We can see that the LTV gradually decrease with cohort age. In January the decline is the modest and in may it's the steepest. Probably because June is relatively weak month for the service. 

Let's find the LTV of the first cohort by adding up the value for each month:

In [1359]:
ltv_january = output.loc[1].sum()
ltv_january 

913.0

On average, each customer from the first cohort brought $913 in revenue over their seven-month liftetime.

## Marketing

### How much money was spent? Overall/per source/over time 

### How much did customer acquisition from each of the sources cost?

### How worthwhile where the investments? (ROI)